Необходимо предсказать по датасету с TV NaN колонки

Unnamed: 0   Год   Месяц  ...            Дата_День next_day                 Дата
0          19  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 00:00:00
1          20  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 01:00:00
2          21  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 02:00:00
3          22  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 03:00:00
4          23  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 04:00:00

[5 rows x 13 columns]

In [ ]:
import pandas as pd
data = pd.read_csv('train.csv')
test = pd.read_csv('test (1).csv')

In [ ]:
train_data = data.drop(['Unnamed: 0','Дата_День','День'],axis=1) # test

train_data['Дата'] = pd.to_datetime(train_data['Дата'])

train_data['weekday'] = train_data['Дата'].apply(lambda x: x.weekday())

train_data = pd.get_dummies(train_data,columns=['Год','Месяц','День','Время','Канал','prime_time'],drop_first=1)
train_data.head()

Все 18+_TVR  Все 55+_TVR  ...  prime_time_2  prime_time_3
0         0.21         0.12  ...             0             0
1         0.71         0.33  ...             0             0
2         1.10         0.59  ...             0             0
3         0.96         0.94  ...             0             0
4         1.94         3.81  ...             0             0

[5 rows x 51 columns]

In [ ]:
data['Время'].unique()

array(['05:00:00 - 06:00:00', '06:00:00 - 07:00:00',
       '07:00:00 - 08:00:00', '08:00:00 - 09:00:00',
       '09:00:00 - 10:00:00', '10:00:00 - 11:00:00',
       '11:00:00 - 12:00:00', '12:00:00 - 13:00:00',
       '13:00:00 - 14:00:00', '14:00:00 - 15:00:00',
       '15:00:00 - 16:00:00', '16:00:00 - 17:00:00',
       '17:00:00 - 18:00:00', '18:00:00 - 19:00:00',
       '19:00:00 - 20:00:00', '20:00:00 - 21:00:00',
       '21:00:00 - 22:00:00', '22:00:00 - 23:00:00',
       '23:00:00 - 24:00:00', '24:00:00 - 25:00:00',
       '25:00:00 - 26:00:00', '26:00:00 - 27:00:00',
       '27:00:00 - 28:00:00', '28:00:00 - 29:00:00'], dtype=object)

In [ ]:
data.shape

(70080, 13)

In [ ]:
data.tail(5)

Unnamed: 0   Год  ... next_day                 Дата
70075       87715  2020  ...     True  2020-11-01 00:00:00
70076       87716  2020  ...     True  2020-11-01 01:00:00
70077       87717  2020  ...     True  2020-11-01 02:00:00
70078       87718  2020  ...     True  2020-11-01 03:00:00
70079       87719  2020  ...     True  2020-11-01 04:00:00

[5 rows x 13 columns]

In [ ]:
train_data = data.drop(['Unnamed: 0','Дата_День'],axis=1)
train_data.head()

Год   Месяц   День  ... Все 55+_Share next_day                 Дата
0  2018  Ноябрь  Day 1  ...          2.00    False  2018-11-01 05:00:00
1  2018  Ноябрь  Day 1  ...          4.90    False  2018-11-01 06:00:00
2  2018  Ноябрь  Day 1  ...          6.49    False  2018-11-01 07:00:00
3  2018  Ноябрь  Day 1  ...          7.41    False  2018-11-01 08:00:00
4  2018  Ноябрь  Day 1  ...         21.51    False  2018-11-01 09:00:00

[5 rows x 11 columns]

In [ ]:
train = pd.get_dummies(train_data,columns=['Год','Месяц','День','Канал'],drop_first=1)
train.head()

Время  Все 18+_TVR  ...  Канал_СТС  Канал_ТНТ
0  05:00:00 - 06:00:00         0.21  ...          0          0
1  06:00:00 - 07:00:00         0.71  ...          0          0
2  07:00:00 - 08:00:00         1.10  ...          0          0
3  08:00:00 - 09:00:00         0.96  ...          0          0
4  09:00:00 - 10:00:00         1.94  ...          0          0

[5 rows x 54 columns]

# Генерация признаков

In [ ]:
# День недели
train['Дата'] = pd.to_datetime(train['Дата'])
train['weekday'] = train['Дата'].apply(lambda x: x.weekday())
# Выходной
train['weekend'] = train['weekday'].apply(lambda x: 1 if x in [5,6] else 0)

In [ ]:
train.head()

Время  Все 18+_TVR  Все 55+_TVR  ...  Канал_ТНТ  weekday  weekend
0  05:00:00 - 06:00:00         0.21         0.12  ...          0        3        0
1  06:00:00 - 07:00:00         0.71         0.33  ...          0        3        0
2  07:00:00 - 08:00:00         1.10         0.59  ...          0        3        0
3  08:00:00 - 09:00:00         0.96         0.94  ...          0        3        0
4  09:00:00 - 10:00:00         1.94         3.81  ...          0        3        0

[5 rows x 56 columns]

In [ ]:
# утренний прайм-тайм — с 6:30 до 10:00;
# дневной — с 12:00 до 14:00;
# вечерний с 16:00 до 21:00.

def prime_time(x):
  if x in ['06:00:00 - 07:00:00','07:00:00 - 08:00:00','08:00:00 - 09:00:00','09:00:00 - 10:00:00']:
    return '1'
  if x in ['12:00:00 - 13:00:00','13:00:00 - 14:00:00']:
    return '2'
  if x in ['16:00:00 - 17:00:00','17:00:00 - 18:00:00','18:00:00 - 19:00:00','19:00:00 - 20:00:00','20:00:00 - 21:00:00']:
    return '3'
  return '0'

def time_age(x):
  if x in [
       '23:00:00 - 24:00:00', '24:00:00 - 25:00:00',
       '25:00:00 - 26:00:00', '26:00:00 - 27:00:00',
       '27:00:00 - 28:00:00', '28:00:00 - 29:00:00']:
       return '1'
  else:
    return '0'

  
train['prime_time'] = train['Время'].apply(lambda x: prime_time(x))
train['night'] = train['Время'].apply(lambda x: time_age(x))
train.head()

Время  Все 18+_TVR  Все 55+_TVR  ...  weekday  weekend  prime_time
0  05:00:00 - 06:00:00         0.21         0.12  ...        3        0           0
1  06:00:00 - 07:00:00         0.71         0.33  ...        3        0           1
2  07:00:00 - 08:00:00         1.10         0.59  ...        3        0           1
3  08:00:00 - 09:00:00         0.96         0.94  ...        3        0           1
4  09:00:00 - 10:00:00         1.94         3.81  ...        3        0           1

[5 rows x 57 columns]

In [ ]:
train = pd.get_dummies(train,columns=['prime_time','Время'],drop_first=1)
# train = train.drop(['Дата'],axis=1)

# Создание выборок

In [ ]:
from sklearn.model_selection import train_test_split
X = train_.drop(['Все 18+_TVR','Все 55+_TVR','Все 18+_Share','Все 55+_Share'],axis=1)
y = train[['Все 18+_TVR','Все 55+_TVR','Все 18+_Share','Все 55+_Share']]
X_train, X_test, y_train, y_test = train_test_split(X,y)

In [ ]:
from sklearn.ensemble import GradientBoostingRegressor
m = GradientBoostingRegressor()

In [ ]:
from sklearn.datasets import make_regression
from sklearn.neighbors import KNeighborsRegressor
from sklearn.ensemble import RandomForestRegressor

neigh = RandomForestRegressor()
neigh.fit(X_train, y_train)
mean_squared_log_error(y_test,neigh.predict(X_test))

0.17343695314025248

In [ ]:
neigh = RandomForestRegressor()
neigh = RegressorChain(model)
neigh.fit(X_train, y_train)
mean_squared_log_error(y_test,absolute(neigh.predict(X_test)))

0:	learn: 1.6923532	total: 8.81ms	remaining: 8.8s
1:	learn: 1.6576417	total: 17.8ms	remaining: 8.87s
2:	learn: 1.6248492	total: 27.1ms	remaining: 9.01s
3:	learn: 1.5909153	total: 35.7ms	remaining: 8.88s
4:	learn: 1.5606324	total: 45.1ms	remaining: 8.98s
5:	learn: 1.5315695	total: 54.1ms	remaining: 8.96s
6:	learn: 1.5027612	total: 63.8ms	remaining: 9.05s
7:	learn: 1.4741940	total: 72.8ms	remaining: 9.03s
8:	learn: 1.4456600	total: 81.8ms	remaining: 9s
9:	learn: 1.4209218	total: 89.9ms	remaining: 8.9s
10:	learn: 1.3962259	total: 99.7ms	remaining: 8.96s
11:	learn: 1.3705747	total: 109ms	remaining: 8.95s
12:	learn: 1.3483358	total: 117ms	remaining: 8.89s
13:	learn: 1.3257103	total: 125ms	remaining: 8.83s
14:	learn: 1.3044253	total: 134ms	remaining: 8.78s
15:	learn: 1.2824828	total: 142ms	remaining: 8.75s
16:	learn: 1.2631059	total: 151ms	remaining: 8.7s
17:	learn: 1.2443018	total: 159ms	remaining: 8.66s
18:	learn: 1.2246193	total: 167ms	remaining: 8.64s
19:	learn: 1.2079593	total: 175ms	re

0.20773173517089397

In [ ]:
m.fit(X_train,y_train['Все 55+_TVR'])

GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                          init=None, learning_rate=0.1, loss='ls', max_depth=3,
                          max_features=None, max_leaf_nodes=None,
                          min_impurity_decrease=0.0, min_impurity_split=None,
                          min_samples_leaf=1, min_samples_split=2,
                          min_weight_fraction_leaf=0.0, n_estimators=100,
                          n_iter_no_change=None, presort='deprecated',
                          random_state=None, subsample=1.0, tol=0.0001,
                          validation_fraction=0.1, verbose=0, warm_start=False)

In [ ]:
from sklearn.metrics import mean_squared_error,mean_absolute_error
mean_squared_error(y_test['Все 55+_TVR'],m.predict(X_test)),mean_absolute_error(y_test['Все 55+_TVR'],m.predict(X_test))

(1.6535970388485424, 0.8415498533910071)

In [ ]:
from xgboost import XGBRegressor
m = XGBRegressor()
m.fit(X_train,y_train['Все 55+_TVR'])
# m.score(X_test,y_test['Все 55+_TVR'])

[08:54:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


XGBRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
             colsample_bynode=1, colsample_bytree=1, gamma=0,
             importance_type='gain', learning_rate=0.1, max_delta_step=0,
             max_depth=3, min_child_weight=1, missing=None, n_estimators=100,
             n_jobs=1, nthread=None, objective='reg:linear', random_state=0,
             reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
             silent=None, subsample=1, verbosity=1)

In [ ]:
from sklearn.metrics import mean_squared_error, mean_absolute_error,mean_squared_log_error
mean_squared_error(y_test['Все 55+_TVR'],m.predict(X_test)),mean_absolute_error(y_test['Все 55+_TVR'],m.predict(X_test))

(1.6612362193920063, 0.841220105298986)

In [ ]:
from numpy import mean
from numpy import std
from numpy import absolute
from sklearn.datasets import make_regression
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedKFold
from sklearn.multioutput import RegressorChain
from sklearn.svm import LinearSVR

model = LinearSVR()
wrapper = RegressorChain(model)
cv = RepeatedKFold(n_splits=10, n_repeats=3, random_state=1)
n_scores = cross_val_score(wrapper, X_train, y_train, scoring='neg_mean_absolute_error', cv=4, n_jobs=-1)
n_scores = absolute(n_scores)
print('MAE: %.3f (%.3f)' % (mean(n_scores), std(n_scores)))

MAE: 2.004 (0.006)


In [ ]:
model = RandomForestRegressor()
wrapper = RegressorChain(model)
wrapper.fit(X_train,y_train)
mean_squared_log_error(y_test,wrapper.predict(X_test))

0.2071303421020661

In [ ]:
from numpy import mean
from numpy import std
from numpy import absolute
from sklearn.datasets import make_regression
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedKFold
from sklearn.multioutput import MultiOutputRegressor
from sklearn.svm import LinearSVR
from sklearn.svm import SVR

model = SVR()
wrapper = MultiOutputRegressor(model)
n_scores = cross_val_score(wrapper, X, y, scoring='neg_mean_squared_log_error', cv=4, n_jobs=-1)
n_scores = absolute(n_scores)
print('MAE: %.3f (%.3f)' % (mean(n_scores), std(n_scores)))

In [ ]:
model = SVR()
wrapper = MultiOutputRegressor(model)
wrapper.fit(X_train,y_train)
mean_squared_log_error(y_test,wrapper.predict(X_test))

In [ ]:
from numpy import mean
from numpy import std
from numpy import absolute
from sklearn.datasets import make_regression
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedKFold
from sklearn.multioutput import MultiOutputRegressor
from sklearn.svm import LinearSVR
from xgboost import XGBRegressor

model = XGBRegressor()
wrapper = MultiOutputRegressor(model)
cv = RepeatedKFold(n_splits=10, n_repeats=3, random_state=1)
n_scores = cross_val_score(wrapper, X, y, scoring='neg_mean_squared_error', cv=4, n_jobs=-1)
n_scores = absolute(n_scores)
print('MAE: %.3f (%.3f)' % (mean(n_scores), std(n_scores)))

MAE: 9.634 (0.547)


# catboost

In [ ]:
!pip install catboost

     |████████████████████████████████| 66.3MB 56kB/s 


In [ ]:
from catboost import CatBoostRegressor

params = {'depth':[6,5,7,8],
          'iterations':[500,1000,1250],
          'learning_rate':[0.02,0.03,0.1], 
          'l2_leaf_reg':[3,5,10,100],
          'border_count':[100,200,250],
          'ctr_border_count':[50,5,10,20,100,200],
}


model = CatBoostRegressor(**{ 'thread_count':-1,
          'loss_function':'MultiRMSE',
          'eval_metric':'MultiRMSE'})
model.grid_search(params,X,
          y,
          verbose=2,      plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))


bestTest = 5.56290364
bestIteration = 499

0:	loss: 5.5629036	best: 5.5629036 (0)	total: 11.1s	remaining: 1h 19m 47s

bestTest = 5.452006829
bestIteration = 499


bestTest = 5.20004838
bestIteration = 499

2:	loss: 5.2000484	best: 5.2000484 (2)	total: 33s	remaining: 1h 18m 37s

bestTest = 5.563154642
bestIteration = 499


bestTest = 5.452138477
bestIteration = 499

4:	loss: 5.4521385	best: 5.2000484 (2)	total: 54.5s	remaining: 1h 17m 37s

bestTest = 5.19810131
bestIteration = 499


bestTest = 5.568186865
bestIteration = 499

6:	loss: 5.5681869	best: 5.1981013 (5)	total: 1m 16s	remaining: 1h 17m 17s

bestTest = 5.456175473
bestIteration = 499


bestTest = 5.204422595
bestIteration = 499

8:	loss: 5.2044226	best: 5.1981013 (5)	total: 1m 38s	remaining: 1h 16m 49s

bestTest = 5.609312656
bestIteration = 499


bestTest = 5.508213443
bestIteration = 499

10:	loss: 5.5082134	best: 5.1981013 (5)	total: 1m 59s	remaining: 1h 16m 27s

bestTest = 5.260962495
bestIteration = 499


bestTest = 5.384

{'cv_results': defaultdict(list,
             {'iterations': [0,
               1,
               2,
               3,
               4,
               5,
               6,
               7,
               8,
               9,
               10,
               11,
               12,
               13,
               14,
               15,
               16,
               17,
               18,
               19,
               20,
               21,
               22,
               23,
               24,
               25,
               26,
               27,
               28,
               29,
               30,
               31,
               32,
               33,
               34,
               35,
               36,
               37,
               38,
               39,
               40,
               41,
               42,
               43,
               44,
               45,
               46,
               47,
               48,
               49,
             

# Best catboost

In [ ]:
# last grid
from catboost import CatBoostRegressor

model = CatBoostRegressor(**{'border_count': 250, 'depth': 8, 'iterations': 1250, 'l2_leaf_reg': 3, 'learning_rate': 0.1, 'thread_count':-1,
          'loss_function':'MultiRMSE',
          'eval_metric':'MultiRMSE'})
model.fit(X,y,verbose=False)

In [ ]:
from catboost import CatBoostRegressor

model = CatBoostRegressor(**{ 'thread_count':-1,
          'loss_function':'MultiRMSE',
          'eval_metric':'MultiRMSE','border_count': 100, 'depth': 8, 'iterations': 1250, 'l2_leaf_reg': 10, 'learning_rate': 0.1})
model.fit(X_train,y_train,verbose=False)

In [ ]:
from sklearn.metrics import mean_squared_log_error
import numpy as np
mean_squared_log_error(y_test,np.absolute(model.predict(X_test))) # Дни недели + Prime_time + Выходной + ноывй подбор параметров

0.16919980136239116

# Bagging

In [ ]:
from sklearn.ensemble import BaggingRegressor
model = CatBoostRegressor(**{'border_count': 250, 'depth': 8, 'iterations': 1250, 'l2_leaf_reg': 3, 'learning_rate': 0.1, 'thread_count':-1,
          'loss_function':'MultiRMSE',
          'eval_metric':'MultiRMSE'})
Xx_train,Xx_test,yy_train,yy_test = train_test_split(X.drop('Дата',axis=1),y,test_size=0.1)
m = BaggingRegressor(model)
m.fit(Xx_train,yy_train)

In [ ]:
from sklearn.metrics import mean_squared_log_error
import numpy as np
mean_squared_log_error(yy_test,np.absolute(m.predict(Xx_test)))

0.17875293025005173

# Predict

In [ ]:
test_data = test.drop(['Unnamed: 0','Дата_День','Дата'],axis=1)
test_data.head()

Год   Месяц   День  ... Все 18+_Share Все 55+_Share  next_day
0  2018  Ноябрь  Day 1  ...           NaN           NaN      True
1  2018  Ноябрь  Day 1  ...           NaN           NaN      True
2  2018  Ноябрь  Day 1  ...           NaN           NaN      True
3  2018  Ноябрь  Day 1  ...           NaN           NaN      True
4  2018  Ноябрь  Day 1  ...           NaN           NaN      True

[5 rows x 10 columns]

In [ ]:
test_data = pd.get_dummies(test_data,columns=['Год','Месяц','День','Время','Канал'],drop_first=1)
X = test_data.drop(['Все 18+_TVR','Все 55+_TVR','Все 18+_Share','Все 55+_Share'],axis=1)
target_values = model.predict(X)

In [ ]:
target_values[0], target_values.shape

(array([1.50791622, 2.22015867, 7.32162509, 8.21336906]), (17640, 4))

In [ ]:
test['Все 18+_TVR'] = [i[0] for i in target_values] 
test['Все 55+_TVR'] = [i[1] for i in target_values] 
test['Все 18+_Share'] = [i[2] for i in target_values]
test['Все 55+_Share'] = [i[3] for i in target_values]

In [ ]:
test.head()

Unnamed: 0   Год   Месяц  ...            Дата_День next_day                 Дата
0          19  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 00:00:00
1          20  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 01:00:00
2          21  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 02:00:00
3          22  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 03:00:00
4          23  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 04:00:00

[5 rows x 13 columns]

In [ ]:
test.tail()

Unnamed: 0   Год  ... next_day                 Дата
17635       87590  2020  ...    False  2020-10-30 19:00:00
17636       87591  2020  ...    False  2020-10-30 20:00:00
17637       87592  2020  ...    False  2020-10-30 21:00:00
17638       87593  2020  ...    False  2020-10-30 22:00:00
17639       87594  2020  ...    False  2020-10-30 23:00:00

[5 rows x 13 columns]

In [ ]:
test.to_csv()

',Unnamed: 0,Год,Месяц,День,Время,Канал,Все 18+_TVR,Все 55+_TVR,Все 18+_Share,Все 55+_Share,Дата_День,next_day,Дата\n0,19,2018,Ноябрь,Day 1,24:00:00 - 25:00:00,ПЕРВЫЙ КАНАЛ,1.5079162234955956,2.2201586699595133,7.321625088851118,8.213369063091811,2018-11-02 00:00:00,True,2018-11-02 00:00:00\n1,20,2018,Ноябрь,Day 1,25:00:00 - 26:00:00,ПЕРВЫЙ КАНАЛ,0.7444584384122115,1.1814920135399942,5.709337683349328,6.462143621217142,2018-11-02 00:00:00,True,2018-11-02 01:00:00\n2,21,2018,Ноябрь,Day 1,26:00:00 - 27:00:00,ПЕРВЫЙ КАНАЛ,0.3830423872413299,0.7450499395506883,4.736537031459852,5.899451460339695,2018-11-02 00:00:00,True,2018-11-02 02:00:00\n3,22,2018,Ноябрь,Day 1,27:00:00 - 28:00:00,ПЕРВЫЙ КАНАЛ,0.22800433536583226,0.52478636445901,4.581616971994194,6.093995498632433,2018-11-02 00:00:00,True,2018-11-02 03:00:00\n4,23,2018,Ноябрь,Day 1,28:00:00 - 29:00:00,ПЕРВЫЙ КАНАЛ,0.1618697890079979,0.3741794242688484,4.570689375480734,5.677235267838339,2018-11-02 00:00:00,True,2018-11-02 04:00:00\n5,43

# Eval

In [ ]:
from catboost import CatBoostRegressor
import pandas as pd
import numpy as np

def eval(data):
    from_file = CatBoostRegressor()
    from_file.load_model("catboost")
    test = pd.read_csv('test.csv')
    test_data = test.drop(['Unnamed: 0','Дата_День','Дата'],axis=1)
    test_data = pd.get_dummies(test_data,columns=['Год','Месяц','День','Время','Канал'],drop_first=1)
    X = test_data.drop(['Все 18+_TVR','Все 55+_TVR','Все 18+_Share','Все 55+_Share'],axis=1)
    target_values = from_file.predict(X)
    test['Все 18+_TVR'] = [i[0] for i in target_values] 
    test['Все 55+_TVR'] = [i[1] for i in target_values] 
    test['Все 18+_Share'] = [i[2] for i in target_values]
    test['Все 55+_Share'] = [i[3] for i in target_values]
    return test.to_csv()

In [ ]:
import io
data_string = eval(1)
data = io.StringIO(data_string)
df = pd.read_csv(data, sep=",")
df.head()

Unnamed: 0                 Дата  Unnamed: 0.1  ...   День         Канал   Месяц
0           0  2018-11-02 00:00:00            19  ...  Day 1  ПЕРВЫЙ КАНАЛ  Ноябрь
1           1  2018-11-02 00:00:00            91  ...  Day 1        РЕН ТВ  Ноябрь
2           2  2018-11-02 00:00:00            43  ...  Day 1      РОССИЯ 1  Ноябрь
3           3  2018-11-02 00:00:00            67  ...  Day 1           СТС  Ноябрь
4           4  2018-11-02 00:00:00           115  ...  Day 1           ТНТ  Ноябрь

[5 rows x 14 columns]

In [ ]:
df.shape

(17640, 14)

In [ ]:
test.head()

Unnamed: 0   Год   Месяц  ...            Дата_День next_day                 Дата
0          19  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 00:00:00
1          20  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 01:00:00
2          21  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 02:00:00
3          22  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 03:00:00
4          23  2018  Ноябрь  ...  2018-11-02 00:00:00     True  2018-11-02 04:00:00

[5 rows x 13 columns]

In [ ]:
from_file = CatBoostRegressor()
from_file.load_model("catboost")
test = pd.read_csv('test.csv')
test_data = test.drop(['Unnamed: 0','Дата_День','Дата'],axis=1)
test_data = pd.get_dummies(test_data,columns=['Год','Месяц','День','Время','Канал'],drop_first=1)
X = test_data.drop(['Все 18+_TVR','Все 55+_TVR','Все 18+_Share','Все 55+_Share'],axis=1)
target_values = from_file.predict(X)

In [ ]:
import numpy as np
import sys
import pandas as pd
np.set_printoptions(threshold=sys.maxsize)

# Итоговая функция, которая запускается на сервере соревнования. Функция запускается исключительно с названием "eval" на сервере.

def eval(data):

    X_train = pd.read_csv("train.csv")
    X_train["Дата"] = pd.to_datetime(X_train["Дата"])
    X_test = pd.read_csv("test.csv")
    X_test["Дата"] = pd.to_datetime(X_test["Дата"])
    X_all = X_train.append(X_test,sort=True)
    X_all.sort_values(by=["Дата","Канал"],inplace=True)

    X_all.set_index("Дата", inplace=True)
    value_cols = ['Все 18+_TVR', 'Все 55+_TVR','Все 18+_Share', 'Все 55+_Share']
    chanels = X_test["Канал"].unique().tolist()
    for n in value_cols:
        #print(n,X_all[n].isna().sum())
        for c in chanels:
            X_all.loc[X_all["Канал"]==c,n] = X_all.loc[X_all["Канал"]==c,n].rolling(
                                                    73,min_periods=1).mean()
        #print("rolls",X_all[n].isna().sum())

    X_res_2 = X_all.loc[
        X_all["Дата_День"].isin(X_test["Дата_День"])].reset_index().sort_values(by=["Дата","Канал"]
        )
    str_x_res = X_res_2.to_csv()
    
    return str_x_res

In [ ]:
train_data

Год    Месяц    День  ... Все 55+_Share next_day                 Дата
0      2018   Ноябрь   Day 1  ...          2.00    False  2018-11-01 05:00:00
1      2018   Ноябрь   Day 1  ...          4.90    False  2018-11-01 06:00:00
2      2018   Ноябрь   Day 1  ...          6.49    False  2018-11-01 07:00:00
3      2018   Ноябрь   Day 1  ...          7.41    False  2018-11-01 08:00:00
4      2018   Ноябрь   Day 1  ...         21.51    False  2018-11-01 09:00:00
...     ...      ...     ...  ...           ...      ...                  ...
70075  2020  Октябрь  Day 31  ...          1.65     True  2020-11-01 00:00:00
70076  2020  Октябрь  Day 31  ...          0.06     True  2020-11-01 01:00:00
70077  2020  Октябрь  Day 31  ...          0.28     True  2020-11-01 02:00:00
70078  2020  Октябрь  Day 31  ...          5.79     True  2020-11-01 03:00:00
70079  2020  Октябрь  Day 31  ...          3.48     True  2020-11-01 04:00:00

[70080 rows x 11 columns]

In [ ]:
def eval(data):
    model = CatBoostRegressor()
    model.load_model("catboost4")
    test = pd.read_csv('test.csv')
    test_data = test.drop(['Unnamed: 0','Дата_День'],axis=1)
    test_data = pd.get_dummies(test_data, columns=['Год', 'Месяц', 'День', 'Канал'], drop_first=1)

    # День недели
    test_data['Дата'] = pd.to_datetime(test_data['Дата'])
    test_data['weekday'] = test_data['Дата'].apply(lambda x: x.weekday())
    # Выходной
    test_data['weekend'] = test_data['weekday'].apply(lambda x: 1 if x in [5, 6] else 0)
    test_data['prime_time'] = test_data['Время'].apply(lambda x: prime_time(x))
    test_data = pd.get_dummies(test_data, columns=['prime_time', 'Время'], drop_first=1)

    X = test_data.drop(['Все 18+_TVR','Все 55+_TVR','Все 18+_Share','Все 55+_Share'],axis=1)
    target_values = np.absolute(model.predict(X))
    test['Все 18+_TVR'] = [i[0] for i in target_values] 
    test['Все 55+_TVR'] = [i[1] for i in target_values] 
    test['Все 18+_Share'] = [i[2] for i in target_values]
    test['Все 55+_Share'] = [i[3] for i in target_values]
    return test.to_csv()

eval(1)

',Unnamed: 0,Год,Месяц,День,Время,Канал,Все 18+_TVR,Все 55+_TVR,Все 18+_Share,Все 55+_Share,Дата_День,next_day,Дата\n0,19,2018,Ноябрь,Day 1,24:00:00 - 25:00:00,ПЕРВЫЙ КАНАЛ,1.3962651968970976,1.877930554877416,7.239748009402049,7.483703676858069,2018-11-02 00:00:00,True,2018-11-02 00:00:00\n1,20,2018,Ноябрь,Day 1,25:00:00 - 26:00:00,ПЕРВЫЙ КАНАЛ,0.550560193691036,0.8268913335345778,5.096541408051344,5.554163668118434,2018-11-02 00:00:00,True,2018-11-02 01:00:00\n2,21,2018,Ноябрь,Day 1,26:00:00 - 27:00:00,ПЕРВЫЙ КАНАЛ,0.2905864005119996,0.5770284249434555,4.35002577793925,5.389444196443773,2018-11-02 00:00:00,True,2018-11-02 02:00:00\n3,22,2018,Ноябрь,Day 1,27:00:00 - 28:00:00,ПЕРВЫЙ КАНАЛ,0.19097104804124063,0.3759553234717786,4.554069815525101,5.747820435500405,2018-11-02 00:00:00,True,2018-11-02 03:00:00\n4,23,2018,Ноябрь,Day 1,28:00:00 - 29:00:00,ПЕРВЫЙ КАНАЛ,0.11334415575316903,0.09199633014200832,4.268535041583342,4.107270617118798,2018-11-02 00:00:00,True,2018-11-02 04:00:00\n5,4